### 参数初始化

In [1]:
%load_ext autoreload
%autoreload 2

import json5
import os
import json
DataSet="SciQAG"

# SciQAG
#  MatSciInstruct

if "__file__" not in globals():
    __file__ = os.path.abspath(".")
print("Running in file:", __file__)
# test_none_path=os.path.join(__file__, 'data','MatSciInstruct_test_none.json')
test_txt_path=os.path.join(__file__,'data', f'{DataSet}.json')

with open(test_txt_path, 'r') as f:
    # Load the JSON5 data from the file
    data= json.load(f)
# with open(test_none_path, 'r') as f:
#     # Load the JSON5 data from the file
#     none_data= json.load(f)

print("Total number of data points:", len(data))
# print("Total number of data points with None in 'answer':", len(none_data))

Running in file: /u01/mengpengyu/dataPipe
Total number of data points: 5814


### 翻译部分问题，用于人工判别

In [2]:
from deep_translator import BaiduTranslator
import json
from model import OpenaiTranslator,V3Translator
from concurrent.futures import ThreadPoolExecutor ,as_completed
# # 创建翻译器并进行翻译
# translator = BaiduTranslator(source='en', 
#                                   target='zh',
#                                   appid="20200702000511635",
#                                   appkey='QkuPegRc_zjsNH0Ytn52'
#                                   )
# # 翻译问题，存储到一个json文件中，后续方便查找
translate_path=os.path.join(__file__, 'data',f'{DataSet}_translate.json')
translate_dict ={}
# i=0
def translate_item(signal_data):

    if DataSet=="SciQAG":
        raw_problem = signal_data['metadata']['question']
        raw_context = signal_data['metadata']['txt']
        raw_answer = signal_data['metadata']['answer']
        
    elif DataSet=="MatSciInstruct":
        raw_problem = signal_data['metadata']['instruction']
        raw_context = signal_data['metadata']['input']
        raw_answer = signal_data['metadata']['output']
    r1_content= signal_data['generations'][0]['answer_content'] 
    translated_problem = V3Translator(raw_problem)
    translated_context = V3Translator(raw_context)
    translated_answer = V3Translator(raw_answer)
    translated_r1_content = V3Translator(r1_content)
    return {
        "raw_context": raw_context,
        "raw_problem": raw_problem,
        "raw_answer": raw_answer,
        "raw_r1_content": r1_content,
        "translated_context": translated_context,
        "translated_problem": translated_problem,
        "translated_answer": translated_answer, 
        "translated_r1_content": translated_r1_content
    }

future_id = {}

with ThreadPoolExecutor(max_workers=100) as executor:
    for signal_data in data[:400]:
        future = executor.submit(translate_item, signal_data)
        future_id[future] = signal_data['id']
        
    for i,future in enumerate(as_completed(future_id.keys())):
        try:
            result = future.result()
            result["qusetion_type"]=-1
            translate_dict[future_id[future]] = result
            if i % 10 == 0:
                print(f"Translated {i} items so far.")
        except Exception as e:
            print(f"Error translating {future_id[future]}: {e}")

print("Translated problems:", translate_dict)
with open(translate_path, 'w') as f:
    json.dump(translate_dict, f, indent=4, ensure_ascii=False)

Translated 0 items so far.
Translated 10 items so far.
Translated 20 items so far.
Translated 30 items so far.
Translated 40 items so far.
Translated 50 items so far.
Translated 60 items so far.
Translated 70 items so far.
Translated 80 items so far.
Translated 90 items so far.
Translated 100 items so far.
Translated 110 items so far.
Translated 120 items so far.
Translated 130 items so far.
Translated 140 items so far.
Translated 150 items so far.
Translated 160 items so far.
Translated 170 items so far.
Translated 180 items so far.
Translated 190 items so far.
Translated 200 items so far.
Translated 210 items so far.
Translated 220 items so far.
Translated 230 items so far.
Translated 240 items so far.
Translated 250 items so far.
Translated 260 items so far.
Translated 270 items so far.
Translated 280 items so far.
Translated 290 items so far.
Translated 300 items so far.
Translated 310 items so far.
Translated 320 items so far.
Translated 330 items so far.
Translated 340 items so f

### 调用模型分类并存放结果

In [ ]:

translate_path=os.path.join(__file__, 'data',f'{DataSet}_translate.json')
with open(translate_path, 'r') as f:
    # Load the JSON5 data from the file
    translate_data= json5.load(f)
from model import call_openai,call_huoshan
import concurrent.futures
from concurrent.futures import ThreadPoolExecutor
import threading # 导入 threading 模块
model_answer_lock = threading.Lock()

prompt_path=os.path.join(__file__, 'prompts','division.txt')
with open(prompt_path, 'r') as f:
    raw_prompt_template = f.read()

model_list= [ 
             "doubao",
            #  "r1", 
            #  "4o",
            #  "v3",
             ]
# model_name = "doubao"
##  "r1"
##  "4o"
##  "doubao"
## "v3"
def process_item(signal_data_item,model_name):
    if DataSet == "MatSciInstruct":
        instruction = signal_data_item['metadata']['instruction']
        input_val = signal_data_item['metadata']['input'] 
        output_val = signal_data_item['metadata']['output']
    elif DataSet == "SciQAG":
        instruction = signal_data_item['metadata']['question']
        input_val = signal_data_item['metadata']['txt'] 
        output_val = signal_data_item['metadata']['answer']
    prompt = raw_prompt_template.replace("{{instruction}}", str(instruction)) \
                                .replace("{{input}}", str(input_val)) \
                                .replace("{{output}}", str(output_val))
    if model_name == "4o":
        _,content = call_openai(prompt)
    else:
        _, content = call_huoshan(prompt,model_name)
    problem_id = signal_data_item['id']
    return content,problem_id
import json
model_answer_path=os.path.join(__file__, 'data',f'{DataSet}_answer.json')
model_answer={}

# # 读取原有文件的测试内容，不进行覆盖
# with open(model_answer_path, 'r') as f:
#     # Load the JSON5 data from the file
#     try:
#         model_answer = json.load(f)
#     except json.JSONDecodeError:
#         print("JSONDecodeError: The file is empty or not a valid JSON.")
import json_repair

def run_use_model(model_name):
    with ThreadPoolExecutor(max_workers=100) as executor:
        future_to_data = {}
        for signal_data_item in data[0:200]:
            future = executor.submit(process_item, signal_data_item,model_name)
            future_to_data[future] = translate_data[signal_data_item['id']]
            # print("future_to_data",future_to_data[future])

        for future in concurrent.futures.as_completed(future_to_data):
            try:
                content ,problem_id= future.result() # 获取 process_item 的返回值
                res_json= json_repair.repair_json(content,return_objects=True)

                    
                with model_answer_lock: # 在访问共享资源 model_answer 之前获取锁
                    if problem_id not in model_answer:
                        model_answer[problem_id] = {
                            "raw_problem": translate_data[problem_id].get('raw_problem', 'N/A'),
                            "raw_context": translate_data[problem_id].get('raw_context', 'N/A'),
                            "translated_problem": translate_data[problem_id].get('translated_problem', 'N/A'),
                            "translated_context": translate_data[problem_id].get('translated_context', 'N/A'),
                            "translated_answer": translate_data[problem_id].get('translated_answer', 'N/A')
                        }
                    model_answer[problem_id][model_name] = res_json
                # 打印结果
                print(content)
                print(f"ID: {problem_id}")
                # print(f"raw problem: {future_to_data['raw_problem']}")
                print(f"translated problem: {translate_data[problem_id]['translated_problem']}")
                print("-" * 50)
            except Exception as exc:
                failed_trans_problem = future_to_data[future]
                print(f"Item with raw problem '{failed_trans_problem['raw_problem']}' generated an exception: {exc}")

# for model_name in model_list:
#     print(f"Running model: {model_name}")
#     run_use_model(model_name)
with ThreadPoolExecutor(max_workers=len(model_list)) as outer_executor:
    for model_name in model_list:
        outer_executor.submit(run_use_model, model_name)
with open(model_answer_path, 'w') as f:
    json.dump(model_answer, f, indent=4, ensure_ascii=False)
print("Model answers saved to:", model_answer_path)

### 计算各个模型和投票结果的一致性

In [24]:
import os
import json
answer_path=os.path.join(__file__, 'data',f'{DataSet}_answer.json')
with open(answer_path, 'r') as f:
    # Load the JSON5 data from the file
    try:
        answer_data = json.load(f)
    except json.JSONDecodeError:
        print("JSONDecodeError: The file is empty or not a valid JSON.")
wrong_answer_path=os.path.join(__file__, 'data',f'{DataSet}_wrong_answer.json')
wrong_answer={}
r1_num = 0
v3_num = 0
doubao_num = 0
for item  in answer_data.items():
    # print(result)
    # print(id)
    result = item[1]
    id= item[0]
    r1_vote=result["r1"]["category"]
    v3_vote=result["v3"]["category"]
    doubao_vote=result["doubao"]["category"]
    if r1_vote == v3_vote and r1_vote == doubao_vote:
        # 三者投票一致，都加分
        r1_num += 1
        v3_num += 1
        doubao_num += 1
    else:
        if r1_vote == v3_vote:
            # r1和gpt投票一致，r1和gpt加分
            r1_num += 1
            v3_num += 1
            
        elif r1_vote == doubao_vote:
            # r1和doubao投票一致，r1和doubao加分
            r1_num += 1
            doubao_num += 1
        elif v3_vote == doubao_vote:
            # gpt和doubao投票一致，gpt和doubao加分
            v3_num += 1
            doubao_num += 1
        else:
            # 三者投票不一致，不加分
            pass
        wrong_answer[id] = result
with open(wrong_answer_path, 'w') as f:
    json.dump(wrong_answer, f, indent=4, ensure_ascii=False)
print("Total number of wrong answer :", len(wrong_answer))
print("r1_rate:", r1_num/ len(answer_data))
print("v3_rate:", v3_num/ len(answer_data))
print("doubao_rate:", doubao_num/ len(answer_data))


Total number of wrong answer : 68
r1_rate: 0.9
v3_rate: 0.835
doubao_rate: 0.915


### 检查知识类内容中，通过规则是否能完全区分

In [51]:
# 读取answer文件，将其中doubao划分为KNOWLEDGE的内容提取出来
# 根据有raw_context是否是空字符串""，也就是有无上下文，划分为两个文件
knowledge_answer_path_txt=os.path.join(__file__, 'data',"knowledge_answer",f'{DataSet}_knowledge_answer_txt.json')
knowledge_answer_path_none=os.path.join(__file__, 'data',"knowledge_answer",f'{DataSet}_knowledge_answer_none.json')
os.makedirs(os.path.join(__file__, 'data',"knowledge_answer"), exist_ok=True)
knowledge_answer_none={}
knowledge_answer_txt={}
for item  in model_answer.items():
    # print(result)
    # print(id)
    result = item[1]
    id= item[0]
    if "doubao" in result:
        doubao_result = result["doubao"]
        if doubao_result["category"] == "KNOWLEDGE":
            if result["raw_context"] == "":
                knowledge_answer_none[id] = result
            else:
                knowledge_answer_txt[id] = result
with open(knowledge_answer_path_none, 'w') as f:
    json.dump(knowledge_answer_none, f, indent=4, ensure_ascii=False)
with open(knowledge_answer_path_txt, 'w') as f:
    json.dump(knowledge_answer_txt, f, indent=4, ensure_ascii=False)
print("Total number of knowledge answer with raw_context is empty:", len(knowledge_answer_none))
print("Total number of knowledge answer with raw_context is not empty:", len(knowledge_answer_txt))

Total number of knowledge answer with raw_context is empty: 24
Total number of knowledge answer with raw_context is not empty: 145


### 制作分类均衡的数据集

In [7]:

# 制作分类均衡的数据集
translate_path=os.path.join(__file__, 'data',f'{DataSet}_translate.json')
with open(translate_path, 'r') as f:
    # Load the JSON5 data from the file
    translate_data= json5.load(f)
balance_data_path=os.path.join(__file__, 'data',"balance",f'{DataSet}_note.json')
os.makedirs(os.path.join(__file__, 'data',"balance"), exist_ok=True)

from model import call_openai,call_huoshan
import concurrent.futures
from concurrent.futures import ThreadPoolExecutor
import threading # 导入 threading 模块
model_answer_lock = threading.Lock()

prompt_path=os.path.join(__file__, 'prompts','division.txt')
with open(prompt_path, 'r') as f:
    raw_prompt_template = f.read()

model_list= [ 
             "doubao",
            #  "r1", 
            #  "4o",
            #  "v3",
             ]
# model_name = "doubao"
##  "r1"
##  "4o"
##  "doubao"
## "v3"
def process_item(signal_data_item,model_name):
    if DataSet == "MatSciInstruct":
        instruction = signal_data_item['metadata']['instruction']
        input_val = signal_data_item['metadata']['input'] 
        output_val = signal_data_item['metadata']['output']
    elif DataSet == "SciQAG":
        instruction = signal_data_item['metadata']['question']
        input_val = signal_data_item['metadata']['txt'] 
        output_val = signal_data_item['metadata']['answer']
    prompt = raw_prompt_template.replace("{{instruction}}", str(instruction)) \
                                .replace("{{input}}", str(input_val)) \
                                .replace("{{output}}", str(output_val))
    if model_name == "4o":
        _,content = call_openai(prompt)
    else:
        _, content = call_huoshan(prompt,model_name)
    problem_id = signal_data_item['id']
    return content,problem_id
import json
model_answer_path=os.path.join(__file__, 'data',f'{DataSet}_answer.json')
model_answer={}

# # 读取原有文件的测试内容，不进行覆盖
# with open(model_answer_path, 'r') as f:
#     # Load the JSON5 data from the file
#     try:
#         model_answer = json.load(f)
#     except json.JSONDecodeError:
#         print("JSONDecodeError: The file is empty or not a valid JSON.")
import json_repair

subjective_dict= {}
knowledge_txt_dict= {}
knowledge_none_dict= {}
reasoning_dict= {}

TARGET_DATA_COUNT=60
def all_categories_filled():
    return (len(subjective_dict) >= TARGET_DATA_COUNT and
            len(knowledge_none_dict) >= TARGET_DATA_COUNT and
            len(knowledge_txt_dict) >= TARGET_DATA_COUNT and
            len(reasoning_dict) >= TARGET_DATA_COUNT)

def run_use_model(model_name):
    with ThreadPoolExecutor(max_workers=100) as executor:
        future_to_data = {}
        for signal_data_item in data[:400]:
            if all_categories_filled():
                print(f"所有分类已收集满 {TARGET_DATA_COUNT} 条数据。提前结束处理。")
                # executor.shutdown(wait=False, cancel_futures=True) # Python 3.9+ 可用于尝试取消正在运行的任务
                break
            future = executor.submit(process_item, signal_data_item,model_name)
            future_to_data[future] = translate_data[signal_data_item['id']]
            # print("future_to_data",future_to_data[future])
        counter = 0
        for future in concurrent.futures.as_completed(future_to_data):          
            # 在处理每个future之前，再次检查是否所有分类都已满
            # 这是为了处理并发情况下，其他future的结果可能已经填满了字典
            if all_categories_filled():
                print(f"所有分类已收集满 {TARGET_DATA_COUNT} 条数据，停止处理剩余已完成任务。")
                # 尝试取消未完成的 future (需要 Python 3.9+ 的 cancel_futures)
                # for f_to_cancel in future_to_data.keys():
                #     if not f_to_cancel.done():
                #         f_to_cancel.cancel()
                break # 跳出 as_completed 循环

            try:
                content ,problem_id= future.result() # 获取 process_item 的返回值
                res_json= json_repair.repair_json(content,return_objects=True)

                model_division = res_json.get("category", "UNKNOWN")
                temp_dict= {
                    "raw_problem": translate_data[problem_id].get('raw_problem', 'N/A'),
                    "raw_context": translate_data[problem_id].get('raw_context', 'N/A'),
                    "raw_answer": translate_data[problem_id].get('raw_answer', 'N/A'),
                    "raw_r1_content": translate_data[problem_id].get('raw_r1_content', 'N/A'),
                    "translated_problem": translate_data[problem_id].get('translated_problem', 'N/A'),
                    "translated_context": translate_data[problem_id].get('translated_context', 'N/A'),
                    "translated_answer": translate_data[problem_id].get('translated_answer', 'N/A'),
                    "translated_r1_content": translate_data[problem_id].get('translated_r1_content', 'N/A'),
                    "qusetion_type": -1,
                }
                if model_division == "SUBJECTIVE" and len(subjective_dict) < TARGET_DATA_COUNT:
                    with model_answer_lock:
                        subjective_dict[problem_id]= temp_dict
                elif model_division == "KNOWLEDGE" and translate_data[problem_id]['raw_context'] == "" and len(knowledge_none_dict) <TARGET_DATA_COUNT:
                    with model_answer_lock:
                        knowledge_none_dict[problem_id]= temp_dict
                elif model_division == "KNOWLEDGE" and translate_data[problem_id]['raw_context'] != "" and len(knowledge_txt_dict) < TARGET_DATA_COUNT:
                    with model_answer_lock:
                        knowledge_txt_dict[problem_id]= temp_dict
                elif model_division == "REASONING" and len(reasoning_dict) < TARGET_DATA_COUNT:
                    with model_answer_lock:
                        reasoning_dict[problem_id]= temp_dict
                else:
                    # 如果已经达到30个，则保存到文件中，并结束程序
                    print(f"分类 '{model_division}' 已满")
                        
                # 打印结果
                print(f"已处理 {counter} 个问题，当前分类：{model_division}")
                counter += 1
                print(len(subjective_dict),len(knowledge_none_dict),len(knowledge_txt_dict),len(reasoning_dict))
                print("-" * 50)
            except Exception as exc:
                failed_trans_problem = future_to_data[future]
                print(f"Item with raw problem '{failed_trans_problem['raw_problem']}' generated an exception: {exc}")

with ThreadPoolExecutor(max_workers=len(model_list)) as outer_executor:
    for model_name in model_list:
        outer_executor.submit(run_use_model, model_name)


已处理 0 个问题，当前分类：KNOWLEDGE
0 0 1 0
--------------------------------------------------
已处理 1 个问题，当前分类：KNOWLEDGE
0 0 2 0
--------------------------------------------------
已处理 2 个问题，当前分类：KNOWLEDGE
0 0 3 0
--------------------------------------------------
已处理 3 个问题，当前分类：KNOWLEDGE
0 0 4 0
--------------------------------------------------
已处理 4 个问题，当前分类：KNOWLEDGE
0 0 5 0
--------------------------------------------------
已处理 5 个问题，当前分类：KNOWLEDGE
0 0 6 0
--------------------------------------------------
已处理 6 个问题，当前分类：REASONING
0 0 6 1
--------------------------------------------------
已处理 7 个问题，当前分类：KNOWLEDGE
0 0 7 1
--------------------------------------------------
已处理 8 个问题，当前分类：REASONING
0 0 7 2
--------------------------------------------------
已处理 9 个问题，当前分类：KNOWLEDGE
0 0 8 2
--------------------------------------------------
已处理 10 个问题，当前分类：KNOWLEDGE
0 0 9 2
--------------------------------------------------
已处理 11 个问题，当前分类：KNOWLEDGE
0 0 10 2
----------------------------------------

In [8]:
import random
print(len(subjective_dict),len(knowledge_none_dict),len(knowledge_txt_dict),len(reasoning_dict))
# 检查是否所有分类都已收集满 30 条数据


all_key_value_pairs = []
# 从每个字典中提取键值对 (problem_id, data_item)
all_key_value_pairs.extend(list(subjective_dict.items()))
all_key_value_pairs.extend(list(knowledge_none_dict.items()))
all_key_value_pairs.extend(list(knowledge_txt_dict.items()))
all_key_value_pairs.extend(list(reasoning_dict.items()))
# 打乱键值对列表的顺序
random.shuffle(all_key_value_pairs)
print("键值对已打乱顺序。")

# 根据打乱后的键值对列表创建一个新的字典
# 这将使得新字典的迭代顺序（以及JSON保存顺序）是随机的
shuffled_balanced_dict = {}
for problem_id, data_item in all_key_value_pairs:
    shuffled_balanced_dict[problem_id] = data_item

print(f"已创建顺序打乱的合并字典，包含 {len(shuffled_balanced_dict)} 条数据。")

# 保存这个顺序打乱的字典到 balance_data_path
try:
    with open(balance_data_path, 'w') as f:
        json.dump(shuffled_balanced_dict, f, indent=4, ensure_ascii=False)
    print(f"顺序打乱的合并字典成功保存到: {balance_data_path}")
except Exception as e:
    print(f"保存顺序打乱的合并字典到 {balance_data_path} 失败: {e}")

1 0 60 60
键值对已打乱顺序。
已创建顺序打乱的合并字典，包含 121 条数据。
顺序打乱的合并字典成功保存到: /u01/mengpengyu/dataPipe/data/balance/SciQAG_note.json


### 读取人工标注数据集，判断模型打标准确性

In [42]:
import json
import os
datasets_path = os.path.join(__file__, 'data','balance', 'labled_datasets.json')
with open(datasets_path, 'r') as f:
    datasets= json.load(f)

from model import call_openai,call_huoshan
import concurrent.futures
from concurrent.futures import ThreadPoolExecutor
import threading # 导入 threading 模块
from collections import defaultdict
model_answer_lock = threading.Lock()

prompt_path=os.path.join(__file__, 'prompts','division.txt')
with open(prompt_path, 'r') as f:
    raw_prompt_template = f.read()

model_list= [ 
             "doubao",
             "r1", 
            #  "4o",
             "v3",
             ]
# model_name = "doubao"
##  "r1"
##  "4o"
##  "doubao"
## "v3"

right_num=defaultdict(int)
sum_num=defaultdict(int)

wrong_answer={}


def process_item(signal_data_item,model_name):
    problem_id=signal_data_item[0]
    signal_data_item = signal_data_item[1]
    instruction = signal_data_item['raw_problem']
    input_val = signal_data_item['raw_context']
    output_val = signal_data_item['raw_answer']
    prompt = raw_prompt_template.replace("{{instruction}}", str(instruction)) \
                                .replace("{{input}}", str(input_val)) \
                                .replace("{{output}}", str(output_val))
    if model_name == "4o":
        _,content = call_openai(prompt)
    else:
        _, content = call_huoshan(prompt,model_name)

    return content,problem_id
import json

model_answer={}
model_wrong_answer=defaultdict(dict)


import json_repair

def run_use_model(model_name):
    counter=0
    with ThreadPoolExecutor(max_workers=100) as executor:
        future_to_data = {}
        for signal_data_item in datasets.items():
            future = executor.submit(process_item, signal_data_item,model_name)
            future_to_data[future] = signal_data_item[1]
            # print("future_to_data",future_to_data[future])

        for future in concurrent.futures.as_completed(future_to_data):
            try:
                content ,problem_id= future.result() # 获取 process_item 的返回值
                res_json= json_repair.repair_json(content,return_objects=True)
                model_division = res_json.get("category", "UNKNOWN")
                if model_division == "UNKNOWN":
                    print(f"Warning: Problem ID {problem_id} has an unknown category.")
                    continue
                # 更新正确率统计
                with model_answer_lock: # 在访问共享资源 model_answer 之前获取锁
                    correct_division = future_to_data[future]['qusetion_type']
                    
                    # # 三分类版本的判断
                    # if correct_division == "Search" or correct_division == "Knowledge":
                    #     correct_division = "Knowledge"
                        
                    if correct_division != "Search" and correct_division != "Knowledge" and correct_division != "Reasoning" and correct_division != "OpenEnded":
                        print(f"Warning: Problem ID {problem_id} has an unexpected question type: {correct_division}.")
                        os.abort("TypeError")
                        
                    
                    if model_division == correct_division:
                        right_num[model_name] += 1
                    else:
                        model_wrong_answer[model_name][problem_id]={
                            "raw_problem": future_to_data[future].get('raw_problem', 'N/A'),
                            "raw_context": future_to_data[future].get('raw_context', 'N/A'),
                            "translated_problem": future_to_data[future].get('translated_problem', 'N/A'),
                            "translated_context": future_to_data[future].get('translated_context', 'N/A'),
                            "translated_answer": future_to_data[future].get('translated_answer', 'N/A'),
                            "problem_type": correct_division,
                            "content": res_json
                        }
                        if problem_id not in model_answer:
                            model_answer[problem_id] = {
                                "raw_problem": future_to_data[future].get('raw_problem', 'N/A'),
                                "raw_context": future_to_data[future].get('raw_context', 'N/A'),
                                "translated_problem": future_to_data[future].get('translated_problem', 'N/A'),
                                "translated_context": future_to_data[future].get('translated_context', 'N/A'),
                                "translated_answer": future_to_data[future].get('translated_answer', 'N/A'),
                                "problem_type": correct_division
                            }
                        model_answer[problem_id][model_name] = res_json
                    sum_num[model_name] += 1
                    
                    # if problem_id not in model_answer:
                    #     model_answer[problem_id] = {
                    #         "raw_problem": future_to_data[future].get('raw_problem', 'N/A'),
                    #         "raw_context": future_to_data[future].get('raw_context', 'N/A'),
                    #         "translated_problem": future_to_data[future].get('translated_problem', 'N/A'),
                    #         "translated_context": future_to_data[future].get('translated_context', 'N/A'),
                    #         "translated_answer": future_to_data[future].get('translated_answer', 'N/A'),
                    #         "problem_type": correct_division
                    #     }
                    # model_answer[problem_id][model_name] = res_json
                # 打印结果
                # global counter
                if counter % 10 == 0:
                    print(f"Processed {counter} items so far for model {model_name}.")
                counter += 1
                # print(content)
                # print(f"ID: {problem_id}")
                # print(f"raw problem: {future_to_data['raw_problem']}")
                # print(f"translated problem: {translate_data[problem_id]['translated_problem']}")
                # print("-" * 50)
            except Exception as exc:
                failed_trans_problem = future_to_data[future]
                print(f"Item with raw problem '{failed_trans_problem['raw_problem']}' generated an exception: {exc}")

# for model_name in model_list:
#     print(f"Running model: {model_name}")
#     run_use_model(model_name)
with ThreadPoolExecutor(max_workers=len(model_list)) as outer_executor:
    for model_name in model_list:
        outer_executor.submit(run_use_model, model_name)
        
model_answer_path=os.path.join(__file__, 'data','model_eval',f'total_answer.json')
os.makedirs(os.path.join(__file__, 'data','model_eval'), exist_ok=True)
with open(model_answer_path, 'w') as f:
    json.dump(model_answer, f, indent=4, ensure_ascii=False)
for model_name in model_list:
    model_wrong_answer_path=os.path.join(__file__, 'data','model_eval',f'{model_name}_wrong_answer.json')
    os.makedirs(os.path.join(__file__, 'data','model_eval'), exist_ok=True)
    with open(model_wrong_answer_path, 'w') as f:
        json.dump(model_wrong_answer[model_name], f, indent=4, ensure_ascii=False)
    print(f"Model answers saved to: {model_wrong_answer_path}")
print("Model answers saved to:", model_answer_path)
for model_name in model_list:
    print(f"Model: {model_name}")
    print(f"Correct Rate: {right_num[model_name] / sum_num[model_name] if sum_num[model_name] > 0 else 0:.2%}")


Processed 0 items so far for model v3.
Processed 0 items so far for model r1.
Processed 10 items so far for model v3.
Processed 20 items so far for model v3.
Processed 30 items so far for model v3.
Processed 0 items so far for model doubao.
Processed 10 items so far for model r1.
Processed 40 items so far for model v3.
Processed 20 items so far for model r1.
Processed 50 items so far for model v3.
Processed 30 items so far for model r1.
Processed 60 items so far for model v3.
Processed 10 items so far for model doubao.
Processed 20 items so far for model doubao.
Processed 40 items so far for model r1.
Processed 30 items so far for model doubao.
Processed 50 items so far for model r1.
Processed 40 items so far for model doubao.
Processed 70 items so far for model v3.
Processed 50 items so far for model doubao.
Processed 60 items so far for model r1.
Processed 80 items so far for model v3.
Processed 60 items so far for model doubao.
Processed 70 items so far for model r1.
Processed 70 it

Traceback (most recent call last):
  File "/u01/mengpengyu/dataPipe/model.py", line 152, in call_huoshan
    response.raise_for_status()  # 捕捉非 2xx 状态码
  File "/u01/mengpengyu/miniconda3/envs/d2l/lib/python3.10/site-packages/requests/models.py", line 1024, in raise_for_status
    raise HTTPError(http_error_msg, response=self)
requests.exceptions.HTTPError: 429 Client Error: Too Many Requests for url: https://ark.cn-beijing.volces.com/api/v3/chat/completions


第 1 次调用失败：429 Client Error: Too Many Requests for url: https://ark.cn-beijing.volces.com/api/v3/chat/completions


Traceback (most recent call last):
  File "/u01/mengpengyu/dataPipe/model.py", line 152, in call_huoshan
    response.raise_for_status()  # 捕捉非 2xx 状态码
  File "/u01/mengpengyu/miniconda3/envs/d2l/lib/python3.10/site-packages/requests/models.py", line 1024, in raise_for_status
    raise HTTPError(http_error_msg, response=self)
requests.exceptions.HTTPError: 429 Client Error: Too Many Requests for url: https://ark.cn-beijing.volces.com/api/v3/chat/completions


第 1 次调用失败：429 Client Error: Too Many Requests for url: https://ark.cn-beijing.volces.com/api/v3/chat/completions
Model answers saved to: /u01/mengpengyu/dataPipe/data/model_eval/doubao_wrong_answer.json
Model answers saved to: /u01/mengpengyu/dataPipe/data/model_eval/r1_wrong_answer.json
Model answers saved to: /u01/mengpengyu/dataPipe/data/model_eval/v3_wrong_answer.json
Model answers saved to: /u01/mengpengyu/dataPipe/data/model_eval/total_answer.json
Model: doubao
Correct Rate: 94.00%
Model: r1
Correct Rate: 96.00%
Model: v3
Correct Rate: 90.00%


### 跑数据